In [20]:
import osmnx as ox
import folium
from shapely.geometry import mapping, Point
import geopandas as gpd
import pandas as pd
import networkx as nx
import json

In [21]:
location = "Exeter, England"

In [22]:
# Extract graph network and seperate into nodes and edges GDF
Gp = ox.graph.graph_from_place(location, network_type="walk")

nodes, edges = ox.graph_to_gdfs(Gp, nodes=True, edges=True)

In [23]:
# Set to flat index for easier traversal
edges = edges.reset_index() 
nodes = nodes.reset_index()

In [44]:
# Feature weights for road safety
feature_weights = {
    "footway": 1.2,
    "pedestrian": 1.8,
    "residential": 1.6,
    "path": 1.0,
    "crossing": 1.4,
    "street_lamp": 2,
    "lit_yes": 2,
    "maxspeed_20": 1.2,
    "maxspeed_30": 1.0,   
    "maxspeed_40": 0.4,
    "maxspeed_40_plus": 0,
    "cctv": 1.8,
    "shop": 1.4
}

In [48]:
def get_speed_weight(maxspeed):
    """Convert speed to numeric mph and return weight."""
    try:
        maxspeed = int(maxspeed.split(" ")[0]) if isinstance(maxspeed, str) else int(maxspeed)
        if maxspeed <= 20:
            return feature_weights["maxspeed_20"]
        elif maxspeed <= 30:
            return feature_weights["maxspeed_30"]
        elif maxspeed <= 40:
            return feature_weights["maxspeed_40"]
        else:
            return feature_weights["maxspeed_40_plus"]
    except (ValueError, TypeError):
        return feature_weights["maxspeed_30"]  # If NaN, assume 30 mph


In [50]:
# Compute pedestrian feature weights for each edge
edges["pedestrian_weight"] = [
    sum(feature_weights.get(feature, 0)  
        for feature in (row["highway"] if isinstance(row["highway"], list) else str(row["highway"]).split(", "))
        if feature in feature_weights)  
    for _, row in edges.iterrows()
]

In [51]:
edges["pedestrian_weight"] += [
    get_speed_weight(row["maxspeed"]) 
    for _, row in edges.iterrows()
]

### Lighting
Below adds lighting locations to edges using geometric buffer

In [54]:
lighting_data = ox.features_from_place(
    location,
    tags={"lit": "yes"}
)

In [59]:
lighting_data = lighting_data.reset_index()

In [14]:
lighting_lines = lighting_data[lighting_data.geom_type == "LineString"]  # Lit roads
lighting_points = lighting_data[lighting_data.geom_type == "Point"]  # Street lamps
lighting_polygons = lighting_data[lighting_data.geom_type == "Polygon"]  # Large lit areas

In [15]:
lighting_points = lighting_points.copy()

x_coords = lighting_points.geometry.x.to_numpy()
y_coords = lighting_points.geometry.y.to_numpy()

lighting_points.loc[:, "nearest_edge"] = ox.distance.nearest_edges(Gp, x_coords, y_coords)

In [16]:
lighting_connected_points = lighting_points[["nearest_edge", "lit"]].copy()

lighting_connected_points[["u", "v", "key"]] = pd.DataFrame(lighting_connected_points["nearest_edge"].tolist(), index=lighting_connected_points.index)

edges = edges.merge(lighting_connected_points.drop(columns=["nearest_edge"]), on=["u", "v", "key"], how="left")


In [17]:
# Convert to projected CRS (meters) for accurate centroid calculation
lighting_lines = lighting_lines.to_crs(epsg=3857)

lighting_lines["geometry_point"] = lighting_lines.geometry.centroid

# Convert back to EPSG:4326 after calculations
lighting_lines = lighting_lines.to_crs(epsg=4326)

x_coords = lighting_lines.geometry_point.x.to_numpy()
y_coords = lighting_lines.geometry_point.y.to_numpy()

lighting_lines["nearest_edge"] = ox.distance.nearest_edges(Gp, x_coords, y_coords)

In [18]:
lighting_connected_lines = lighting_lines[["nearest_edge", "lit"]].copy()

lighting_lines[["u", "v", "key"]] = pd.DataFrame(lighting_lines["nearest_edge"].tolist(), index=lighting_lines.index)

edges = edges.merge(
    lighting_connected_points.drop(columns=["nearest_edge"]),
    on=["u", "v", "key"],
    how="left",
    suffixes=("", "_new") 
)

edges.loc[edges["lit_new"] == "yes", "lit"] = "yes"

edges = edges.drop(columns=["lit_new"])

In [19]:
lighting_polygons = lighting_polygons.copy()

lighting_polygons["geometry"] = lighting_polygons.geometry.boundary

matched_lighting_polygons = gpd.sjoin(
    edges, lighting_polygons[["geometry", "lit"]],
    how="left", predicate="intersects"
)

In [20]:
matched_lighting_polygons = matched_lighting_polygons.drop(columns=["index_right", "lit_left"], errors="ignore")

edges = edges.merge(
    matched_lighting_polygons[["u", "v", "key", "lit_right"]],  
    on=["u", "v", "key"],
    how="left",
)

edges.loc[edges["lit_right"] == "yes", "lit"] = "yes"

edges = edges.drop(columns=["lit_right"])

In [21]:
# Ensure no NaN values
edges["lit"] = edges["lit"].fillna("no")

In [22]:
edges.loc[edges["lit"] == "yes", "pedestrian_weight"] += feature_weights["lit_yes"]

### CCTV
Below adds CCTV locations to edges using geometric buffer

In [61]:
cctv_locations = ox.features_from_place(
    location,
    tags={"man_made": "surveillance"}  
)
cctv_locations = cctv_locations.reset_index()

In [25]:
cctv_locations = cctv_locations.to_crs(epsg=3857)

cctv_locations["buffer"] = cctv_locations.geometry.buffer(50) 

cctv_locations = cctv_locations.to_crs(epsg=4326)

cctv_locations = cctv_locations.set_geometry("buffer")

In [27]:
edges = edges.to_crs(cctv_locations.crs)

matched_cctv_edges = gpd.sjoin(
    edges, cctv_locations[["buffer"]],  
    how="left", predicate="intersects"
)

In [28]:
# Initialize CCTV coverage column
edges["covered_by_cctv"] = "no"

# Ensure only edges that intersect with CCTV coverage areas are updated
covered_edges = matched_cctv_edges.dropna(subset=["index_right"]).index 
edges.loc[covered_edges, "covered_by_cctv"] = "yes"

In [29]:
edges.loc[edges["covered_by_cctv"] == "yes", "pedestrian_weight"] += feature_weights["cctv"]

### Shops
Below adds shop locations to edges using geometric buffer

In [63]:
shops = ox.features_from_place(
    location, 
    tags={"shop": True}  
)
shops = shops.reset_index()

In [51]:
shops = shops.to_crs(epsg=3857)  # Convert to meters for accurate buffering

shops["buffer"] = shops.geometry.buffer(50)  

shops = shops.to_crs(epsg=4326)

shops = shops.set_geometry("buffer")

In [53]:
edges = edges.to_crs(shops.crs)

matched_shop_edges = gpd.sjoin(
    edges, shops[["buffer"]],  
    how="left", predicate="intersects"
)

In [55]:
edges["near_shop"] = "no"

covered_edges = matched_shop_edges.dropna(subset=["index_right"]).index  
edges.loc[covered_edges, "near_shop"] = "yes"

### Routing

In [58]:

for u, v, key, data in Gp.edges(keys=True, data=True):
    row = edges[(edges["u"] == u) & (edges["v"] == v) & (edges["key"] == key)]
    if not row.empty:
        pedestrian_weight = row.iloc[0]["pedestrian_weight"]
        data["weight"] = 1 / pedestrian_weight if pedestrian_weight > 0 else float("inf")

In [59]:
# Test coords
start_point = (50.72119, -3.52627)  
end_point = (50.72608, -3.53399)

start_node = ox.distance.nearest_nodes(Gp, X=start_point[1], Y=start_point[0])
end_node = ox.distance.nearest_nodes(Gp, X=end_point[1], Y=end_point[0])

In [60]:
safest_route = nx.shortest_path(Gp, source=start_node, target=end_node, weight="weight")

In [61]:
shortest_route = nx.shortest_path(Gp, source=start_node, target=end_node, weight="length")

In [62]:
# Create a Folium map centered on the start location
route_map3 = folium.Map(location=start_point, zoom_start=14)

# Extract route coordinates
shortest_route_coords = [(Gp.nodes[node]["y"], Gp.nodes[node]["x"]) for node in shortest_route]
safest_route_coords = [(Gp.nodes[node]["y"], Gp.nodes[node]["x"]) for node in safest_route]

# Plot the Shortest Route (Red)
folium.PolyLine(
    locations=shortest_route_coords,
    color="red",
    weight=5,
    opacity=0.8,
    popup="Shortest Route"
).add_to(route_map3)

# Plot the Safest Route (Green)
folium.PolyLine(
    locations=safest_route_coords,
    color="green",
    weight=5,
    opacity=0.8,
    popup="Safest Route"
).add_to(route_map3)

# Display the map
route_map3


In [ ]:
#route_map2.save("osm_demo3.html")

In [63]:
edges.drop(columns=["tunnel", "service", "lanes", "name", "bridge", "junction", "landuse"], inplace=True)

In [64]:
edges.to_file('edges_with_pedestrian_weights.gpkg', driver='GPKG')


In [106]:
pedestrian_edges = gpd.read_file("edges_with_pedestrian_weights.gpkg")

In [111]:
pedestrian_edges = pedestrian_edges.groupby(["u", "v", "key"], as_index=False).agg({
    "osmid": "first",   # Keep first osmid (or convert to list if multiple exist)
    "oneway": "first",
    "reversed": "first",
    "length": "mean",  # Average length (adjust as needed)
    "access": "first",
    "est_width": "first",
    "pedestrian_weight": "mean",
    "geometry": "first"  # Keep one geometry
})

In [119]:
pedestrian_edges = gpd.GeoDataFrame(pedestrian_edges, geometry="geometry", crs="EPSG:4326")


In [113]:
pedestrian_edges = pedestrian_edges.set_index(["u", "v", "key"])

In [121]:
g_rebuild = ox.graph_from_gdfs(nodes, pedestrian_edges)

In [87]:
# Initialize Folium map centered on your location
map_center = [50.7236, -3.5275]  
feature_map = folium.Map(location=map_center, zoom_start=14, 
    tiles="CartoDB Positron")

# Create separate layers for toggling
#roads_layer = folium.FeatureGroup(name="Road Types").add_to(feature_map)
lighting_layer = folium.FeatureGroup(name="Lighting").add_to(feature_map)
cctv_layer = folium.FeatureGroup(name="CCTV").add_to(feature_map)
shop_layer = folium.FeatureGroup(name="Shops").add_to(feature_map)

# 1. LIGHTING: Handle Points, Lines, and Polygons
for _, row in lighting_data.iterrows():
    geom = row.geometry
    
    if geom.geom_type == "Point":
        folium.CircleMarker(
            location=[geom.y, geom.x],
            radius=4,
            color="yellow",
            fill=True,
            fill_opacity=0.8,
            popup="Street Lamp"
        ).add_to(lighting_layer)
    
    elif geom.geom_type == "LineString":
        folium.PolyLine(
            locations=[(coord[1], coord[0]) for coord in geom.coords],
            color="green",
            weight=3,
            popup="Lit Road"
        ).add_to(lighting_layer)
    
    elif geom.geom_type == "Polygon":
        folium.Polygon(
            locations=[(coord[1], coord[0]) for coord in geom.exterior.coords],
            color="gold",
            fill=True,
            fill_opacity=0.3,
            popup="Lit Area"
        ).add_to(lighting_layer)

# 2. CCTV LOCATIONS
for _, row in cctv_locations.iterrows():
    geom = row.geometry
    if geom.geom_type == "Point":
        folium.Marker(
            location=[geom.y, geom.x],
            icon=folium.Icon(color="red", icon="camera", prefix="fa"),
            popup="CCTV Camera"
        ).add_to(cctv_layer)

# 3. SHOPS
for _, row in shops.iterrows():
    geom = row.geometry
    if geom.geom_type == "Point":
        shop_type = row.get("shop", "Shop")
        folium.Marker(
            location=[geom.y, geom.x],
            icon=folium.Icon(color="green", icon="shopping-cart", prefix="fa"),
            popup=f"Shop: {shop_type}"
        ).add_to(shop_layer)

# Add layer control so user can toggle visibility
folium.LayerControl().add_to(feature_map)

# Display in Jupyter or save
feature_map

In [90]:
feature_map.save("feature_map.html")